# Импорт библиотек

In [1]:
import warnings
from pathlib import Path

import torch
from torch import nn, optim
from torch.utils.data import DataLoader

from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix

from tqdm.notebook import tqdm

from utils import *

warnings.filterwarnings("ignore")

# Конфигурация

In [2]:
# Устройство, на котором будут происходить все вычисления
device = "cuda" if torch.cuda.is_available() else "cpu"

# Путь до датасета с npz архивами
dataset_path = "D:/ProjectsData/Chest X-Ray Images (Pneumonia)/chest_xray/chest_xray"

# Имя базовой модели для классификатора изображений
image_model_type = "convnext"
# Количество предсказываемых классов
num_classes = len(inference_dict)
# Загрузка весов классификатора изображений
pretrained = True
# Заморозка весов классификатора изображений
freeze_weight = False

# Количество обучающих эпох
num_epochs = 10
# Размер батча при обучении
batch_size = 3

# Пути сохранения и загрузки чекпоинта
save_path = "./models/convnext.pt"
checkpoint_path = None

# Инициализация необходимых переменных

In [3]:
print(device)
if device == "cuda":
    print(torch.cuda.get_device_name())
    torch.set_default_tensor_type('torch.cuda.FloatTensor')

# Список путей до изображений
image_path_array = list(Path(dataset_path).glob("**/*.jpeg"))

# Разделение выборки на обучающую, тестовую, валидационную в соотношении 0.8/0.1/0.1
train_path, test_val_path = train_test_split(image_path_array, train_size=0.8, random_state=42)
test_path, val_path = train_test_split(test_val_path, train_size=0.5, random_state=42)

# Инициализация классификатора изображений и препроцессинга изображения
model, image_preprocess = get_image_model(name=image_model_type, pretrained=pretrained,
                                                freeze_weight=freeze_weight, num_classes=num_classes)

# Инициализация датасетов
train_dataset = ChestXRayDataset(path_array=train_path, image_preprocess=image_preprocess, augmented=True, device=device)
test_dataset = ChestXRayDataset(path_array=test_path, image_preprocess=image_preprocess, augmented=False, device=device)
val_dataset = ChestXRayDataset(path_array=val_path, image_preprocess=image_preprocess, augmented=False, device=device)

print(f"Количество наборов данных на:\nОбучение: {len(train_dataset)}\nТестирование: {len(test_dataset)}\nВалидацию: {len(val_dataset)}")

# Инициализация класса функции потерь
criterion = nn.CrossEntropyLoss()
# Инициализация класса оптимизатора
optimizer = optim.Adam(model.parameters(), lr=0.001)

# Загрузка чекпоинта
# Стартовая эпоха
start_epoch = 0
# Переменная для сравнения точности моделей и сохранения лучшей
last_best_acc = 0
if checkpoint_path:
    checkpoint = torch.load(checkpoint_path)
    model.load_state_dict(checkpoint["model"])
    criterion.load_state_dict(checkpoint["loss"])
    optimizer.load_state_dict(checkpoint["optimizer"])
    start_epoch = checkpoint['epoch'] - 1
    last_best_acc = checkpoint["last_best_acc"]
    print(f"Чекпоинт загружен, сохраненная эпоха: {start_epoch}, точность: {last_best_acc}")

cuda
NVIDIA GeForce RTX 3080
Количество наборов данных на:
Обучение: 4684
Тестирование: 586
Валидацию: 586


# Обучение

In [4]:
model.to(device)

# Загрузчик данных для обучения и валидации
dataloader_train = DataLoader(train_dataset, batch_size=batch_size, generator=torch.Generator(device=device),
                              shuffle=True, drop_last=True)
dataloader_val = DataLoader(val_dataset, generator=torch.Generator(device=device))

# Контроллеры скорости обучения
scheduler1 = optim.lr_scheduler.ExponentialLR(optimizer, gamma=0.9)
scheduler2 = optim.lr_scheduler.MultiStepLR(optimizer,
                                            milestones=list(range(start_epoch, start_epoch + num_epochs, 3)),
                                            gamma=0.5)
# Переменные для сохранения истории изменения потерь и точности
train_loss_arr, val_loss_arr = [], []
train_acc_arr, val_acc_arr = [], []
for epoch in tqdm(range(start_epoch, start_epoch + num_epochs)):
    print(f"Эпоха {epoch + 1}/{start_epoch + num_epochs}")
    # Режим обучения модели
    model.train()
    # Переменные для подсчета точности и потерь
    epoch_train_loss, epoch_val_loss = 0, 0
    y_true, y_pred = [], []

    # Процесс обучения
    for inputs, labels in tqdm(dataloader_train):
        # Обнуление градиента
        optimizer.zero_grad()

        # Предсказание
        logits = model(inputs)
        predictions = logits.argmax(dim=1)

        # Вызов функции потерь
        train_loss = criterion(logits, labels)

        # Дифференцирование с учетом параметров
        train_loss.backward()
        # Шаг оптимизации
        optimizer.step()

        # Суммирование потерь
        epoch_train_loss += train_loss.item()

        # Записывание предсказанных и действительных диагнозов
        y_true.extend(labels.cpu())
        y_pred.extend(predictions.cpu())

    # Вывод метрик обучения эпохи
    print(classification_report(y_true, y_pred))
    # Сохранение значений потерь и точности в историю
    train_loss_arr.append(epoch_train_loss / len(train_dataset))
    train_acc_arr.append(accuracy_score(y_true, y_pred))

    # Уменьшение скорости обучения
    scheduler1.step()
    scheduler2.step()

    # Режим валидации модели
    model.eval()

    # Переменные для подсчета точности
    y_true, y_pred = [], []
    # Процесс валидации модели
    # Локальное отключение вычисления градиента
    with torch.no_grad():
        for inputs, labels in tqdm(dataloader_val):
            # Предсказание
            inputs, labels
            logits = model(inputs)
            predictions = logits.argmax(dim=1)
            # Вызов функции потерь
            val_loss = criterion(logits, labels)
            # Суммирование потерь
            epoch_val_loss += val_loss.item()

            y_true.extend(labels.cpu())
            y_pred.extend(predictions.cpu())

    print(classification_report(y_true, y_pred))

    # Вывод потерь и текущей скорости обучения
    for param_group in optimizer.param_groups:
        lr = param_group['lr']
    print(
        f"loss (обучение): {epoch_train_loss / len(train_dataset):.4f}\n"
        f"loss (валидация): {epoch_val_loss / len(val_dataset):.4f}\n"
        f"Скорость обучения: {lr}"
    )
    
    # Текущая валидационная точность
    current_acc = accuracy_score(y_true, y_pred)
    # Сохранение значений потерь и точности в историю
    val_loss_arr.append(epoch_val_loss / len(val_dataset))
    val_acc_arr.append(current_acc)
    
    # Сохранение модели
    if current_acc > last_best_acc and save_path:
        torch.save({
            'epoch': epoch + 1,
            'model': model.state_dict(),
            'optimizer': optimizer.state_dict(),
            'loss': criterion.state_dict(),
            'last_best_acc': current_acc,
        }, save_path)
        print(f"Сохранение модели. Текущая валидационная точность: {current_acc:.4f}")
        last_best_acc = current_acc

  0%|          | 0/10 [00:00<?, ?it/s]

Эпоха 1/10


  0%|          | 0/1561 [00:00<?, ?it/s]

              precision    recall  f1-score   support

           0       0.72      0.68      0.70      1252
           1       0.50      0.18      0.26      1203
           2       0.61      0.84      0.71      2228

    accuracy                           0.63      4683
   macro avg       0.61      0.57      0.56      4683
weighted avg       0.61      0.63      0.59      4683



  0%|          | 0/586 [00:00<?, ?it/s]

...

              precision    recall  f1-score   support

           0       0.92      0.95      0.94       167
           1       0.64      0.44      0.52       127
           2       0.79      0.88      0.83       292

    accuracy                           0.80       586
   macro avg       0.78      0.76      0.76       586
weighted avg       0.79      0.80      0.79       586

loss (обучение): 0.1485
loss (валидация): 0.4714
Скорость обучения: 3.8742048900000014e-08
Эпоха 10/10


  0%|          | 0/1561 [00:00<?, ?it/s]

              precision    recall  f1-score   support

           0       0.93      0.95      0.94      1252
           1       0.71      0.56      0.63      1202
           2       0.80      0.87      0.83      2229

    accuracy                           0.81      4683
   macro avg       0.81      0.80      0.80      4683
weighted avg       0.81      0.81      0.81      4683



  0%|          | 0/586 [00:00<?, ?it/s]

              precision    recall  f1-score   support

           0       0.92      0.95      0.94       167
           1       0.64      0.44      0.52       127
           2       0.79      0.88      0.83       292

    accuracy                           0.80       586
   macro avg       0.78      0.76      0.76       586
weighted avg       0.79      0.80      0.79       586

loss (обучение): 0.1465
loss (валидация): 0.4712
Скорость обучения: 3.486784401000001e-08


## Графики процесса обучения

In [5]:
import plotly.graph_objects as go

# Создаем графический объект
fig = go.Figure()

# Добавляем линию графика для первого массива
fig.add_trace(go.Scatter(x=list(range(len(train_loss_arr))), y=train_loss_arr, mode='lines', name='Обучение'))

# Добавляем линию графика для второго массива
fig.add_trace(go.Scatter(x=list(range(len(val_loss_arr))), y=val_loss_arr, mode='lines', name='Валидация'))

# Настраиваем метки осей и заголовок графика
fig.update_layout(width=800, height=600, xaxis_title='Эпоха', yaxis_title='Потери', title='График потерь при обучении модели')

# Отображаем график
fig.show()

In [6]:
# Создаем графический объект
fig = go.Figure()

# Добавляем линию графика для первого массива
fig.add_trace(go.Scatter(x=list(range(len(train_acc_arr))), y=train_acc_arr, mode='lines', name='Обучение'))

# Добавляем линию графика для второго массива
fig.add_trace(go.Scatter(x=list(range(len(val_acc_arr))), y=val_acc_arr, mode='lines', name='Валидация'))

# Настраиваем метки осей и заголовок графика
fig.update_layout(width=800, height=600, xaxis_title='Эпоха', yaxis_title='Точность', title='График точности при обучении модели')

# Отображаем график
fig.show()

# Тестирование

In [8]:
# Загрузка лучшей модели
model.load_state_dict(torch.load(save_path)["model"])

model.to(device)
# Режим валидации модели
model.eval()
# Загрузчик данных для тестирования
dataloader = DataLoader(test_dataset, generator=torch.Generator(device=device), drop_last=True)

# Переменные для подсчета точности
y_true, y_pred = [], []
# Локальное отключение вычисления градиента
with torch.no_grad():
    for inputs, labels in tqdm(dataloader):
        # Предсказание
        outputs = model(inputs)
        predictions = outputs.argmax(dim=1)

        y_true.extend(labels.cpu())
        y_pred.extend(predictions.cpu())

# Вывод метрик
print(classification_report(y_true, y_pred))
# Вывод матрицы ошибок
print(confusion_matrix(y_true, y_pred))

  0%|          | 0/586 [00:00<?, ?it/s]

              precision    recall  f1-score   support

           0       0.93      0.98      0.96       164
           1       0.82      0.60      0.69       163
           2       0.80      0.90      0.85       259

    accuracy                           0.84       586
   macro avg       0.85      0.83      0.83       586
weighted avg       0.84      0.84      0.83       586

[[161   2   1]
 [  7  98  58]
 [  5  20 234]]
